# INVENTORY DAYS - Chanllegue was taken by MFrancys

Antes de abordar las preocupaciones de los stakholders y realizar la revisión del codigo con elobjeto de proponer mejorar en la generación del Modelo de ML, es necesario realizar  un cambio en la forma de resolver el problema de predecir el tiempo en el cual permanecerán en el inventario los automóviles (Días en el inventario o DI) antes de venderse.

La variable objetivo de este problema es predecir el tiempo de venta de un automovil considerando sus caracteristicas fisicas y precio con base a un cojunjo de información historicas de las caracteristicas de los automviles y el respectivo label sobre el tiempo que se mantuvo en el inventario antes de venderse. En el campo de MAchine Learning, este tipo de problema es considerado como Suprevised learning.

No obstanste, dado las particulares inherentes al problema que se trata de resolver se intesifican las debiliddads de las soluciones de Machine Learning mediante Supervised Learning, las cuales comentare acontinuación: 
    
1. La naturaleza de los datos de este problema: La mayor parte de los datos que conforman el dataset proporcionado para abordadr este problema son considerados como datos del tipo censurados a la derecha. Los datos censurados a la derecha son aquellos que comprenden información de eventos que no han ocurrido durante el periodo de estudio. Por ejemplo, en este caso de estudio, un automovil que tiene solo 10 días en el inventario, al momento de realizar el estudio, no puede categorizarse como no vendida, dado que posee un tiempo reducido en el mercado Por lo cual, que no haya sido vendida durante el tiempo de estudio, no implica que no pueda ser vendida a en un timpoe posterior a la realización del estudio, con un tiempo mayor de exposición en el mercado. 
   
   <img src="images/example_inventory_days.png">
   
   No obstante, el modelo implementado en el codigo original es un algortimo de machine learning supervisado denominado, pero una de una de las limitaciones de estos algoritmos es la dificultad de manejar adecuadamente la información censurada y el factor de tiempo asociado. Con base a esto, se propone el desarrollo de un modelo alternativo, bajo el enfoque de <a href="https://www.notion.so/truehome/Shortlist-Version-2-0-7158f764bc0f44169a468479a193a7ea#f4fe430384b24db9a59ca3f126db9137">análisis de sobrevivencia</a>, esta rama de la estadísticas ha desarrollado técnicas que lidian con estos dos elementos simultáneamente. A su vez, este cambio de enfoque para resolver este problema deriva en la re-formulación de varios aspectos del modelo:
    
    a. Input -> Cambio en la variable objetivo. 
    
    Antes, es necesario introducir un termino adicional:
    
    - Tiempo hasta el evento: Se considera el tiempo hasta el evento al tiempo necesario para que ocurra un evento desde el inicio del estudio. Ejemplo, en nuestro caso, si ocurre la venta de un automovil, el tiempo hasta el evento es el tiempo entre la incorporación del automovil al inventario hasta que ocurrió la venta.

    > "*Para un problema de supervivencia, el tiempo hasta el evento se conoce precisamente para aquellos casos en que el evento ocurrió durante el período de estudio. Para las instancias restantes, dado que podemos perderles la pista durante el tiempo de observación o su tiempo hasta el evento es mayor que el tiempo observado, solo podemos tener el tiempo censurado." -*[https://www.linkedin.com/pulse/survival-analysis-machine-learning-perspective-dibyanshu-dwivedi/](https://www.linkedin.com/pulse/survival-analysis-machine-learning-perspective-dibyanshu-dwivedi/)

    En un modelo clásico de clasificación binaria, la variable objetivo es una variable dependiente binaria con la información sobre si un evento ocurrió o no. En un problema bajo el enfoque de análisis de supervivencia, un factor de tiempo es incluido en la variable objetivo de la siguiente manera:

        $$y(i) = ( t(i), e(i) )$$

    donde:    

    - *i* representa una instancia de la muestra
    - *t(i)* denota tanto el tiempo hasta el evento si la instancia es no-censurada como el tiempo  de censurada para una instancia censurada.
    - *e(i)* es una indicador del evento, él cual toma el valor de 1 para la ocurrencia del evento y 0 para un evento censurado.

    En este caso de estudio, los elementos mencionados previamente tienen la siguiente representación:

    - *i* representa un automovil.
    - *t(i)* denota tanto el tiempo hasta el evento, es decir, cuando se genera la venta del automovil, este tiempo compreende el periodo desde su incorporación en el inventario  hasta la venta de l vehiculo, como el tiempo de censurada, que representa el tiempo en el cual ha permanecido un automovil en el inventario.
    - *e(i)* toma el valor de 1 si el vehiculo se vendió y 0 en caso contrario.
        
    Al realizar el cambio de la variable objetivo, es posible incorporar mayor cantidad de datos para alimentar el modelos. Dado que anteriormente se excluia del entrenamiento a aquellos vehiculos que no se habian vendido para el momento del estudio. Este conjunto de datos omitidos representan alrededor del 17,3% de los dats historicos de vehiculos que han sido incorparados en el inventario.

    b. Modelamiento -> Incoporación de algoritmos de Machine Learning para el análisis de supervivencia. 
    Los datos, bajo el enfoque de análisis de supervivencia, se analizan comúnmente utilizando métodos que se basan en suposiciones restrictivas y a menudo son paramétricos, por lo cual, los efectos no lineales de las variables deben ser modelados por transformaciones o se deben incluir funciones de bases especializadas. Además, identificar interacciones, especialmente aquellas que involucran variables múltiples, también es problemático. En contraste, estas dificultades se puede manejar automáticamente usando algoritmos de machine learning, dado sus ventajas potenciales sobre los métodos estadísticos estándar, como su capacidad para modelar relaciones no lineales y construir modelos simbólicos e interpretables. No obstante, a pesar de estas ventajas, una de las limitaciones de estos algoritmos es la dificultad de manejar adecuadamente la información censurada y el factor de tiempo asociado. Dicho esto, hay muchos métodos de aprendizaje automático que se adaptan a la necesidad del problema de supervivencia. La estructura general de los algoritmos sigue siendo la misma. Las diferencias clave se encuentran en la función objetivo general y el criterio para evaluar el evento en los puntos de decisión. Por ejemplo, el árbol de decisión está adaptado para el análisis de supervivencia como árbol de supervivencia. La principal diferencia entre un árbol de supervivencia y el árbol de decisión estándar está en la elección del criterio de división de los nodos.
> "*Survival trees are binary trees grown by recursive splitting of tree nodes. A tree is grown starting at the root node, which is the top of the tree comprising all the data. Using a predetermined survival criterion, the root node is split into two daughter nodes: a left and right daughter node. In turn, each daughter node is split with each split giving rise to left and right daughters. The process is repeated in a recursive fashion for each subsequent node.
A good split for a node maximizes survival difference between daughters. The best split for a node is found by searching over all possible x variables and split values c, and choosing that x∗ and c∗ that maximizes survival difference. By maximizing survival difference, the tree pushes dissimilar cases apart. Eventually, as the number of nodes increase, and dissimilar cases become separated, each node in the tree becomes homogeneous and is populated by cases with similar survival." -* [https://projecteuclid.org/euclid.aoas/1223908043](https://projecteuclid.org/euclid.aoas/1223908043).
Para esta propuesta, se utilizará una implementación del modelo *Random Survival Forests* del paquete *scikit-survival*, él cual es un módulo de Python para el análisis de supervivencia construido sobre scikit-learn.


    c. Output -> The predicted survival function. Está función decreciente determina la probabilidad de que el evento de interés no haya ocurrido en el tiempo *t* y se modela de la siguiente manera:

    $$S(t) = P(T> t)$$

    Donde:

    - *T* denota una variable aleatoria continua no negativa que corresponde al tiempo de supervivencia.

    Las propiedades de esta funciones incluyen los siguientes escenarios:

    - Si *t=0*, por lo cual, *S(0)*, entonces la probabilidad es igual a 1. 

    - Si *t=∞,* por lo cual, *S(∞)*, entonces la probabilidad es igual a 0. 

    - Si *S(t)*, entonces la probabilidad decrece cuando t tiende a infinito.

    Con esta función se puede coplementar la tarea de predecir el numero de dias en el invetario de un automovil, al tener una visión más detallada de estas predecciones.

        
2. Dataset is partially labeled: El dataset proporcionado comprende iformación historica de 20000 vehiculos que has ingresado a inventario. No obstante, solo de 8328 del total de registros se tiene información de su statu, es decir, si han sido vendidos o no, y de los días que han permanecido en inventario. Por lo cual si abordamos este problema como un modelo de machine learning supervisado estaremos dejando aproximandamente 58% de la informaciñon suminastrada en el dataset para alimentar el modelo.
    Por lo cual, el desafio en este punto es etiquetar de manera eficiente observaciones sin etiquetar mientras se aprovecha la información en el conjunto etiquetado. Con el aprendizaje supervisado, se tendria que desechar la mayoría de los datos proporcionados, y  no se podria aprovechar de mejor manera las pocas etiquetas que se tienen. Mientras, son el aprendizaje no supervisado, se tendría la mayoría de los datos con los que trabajar, pero no sabríamos cómo aprovechar las pocas etiquetas que tenemos.
    Por lo tanto, el campo del aprendizaje semisupervisado combina los beneficios del aprendizaje supervisado y no supervisado, aprovechando las pocas etiquetas que tenemos.
    En sintensis, para resolver este problema se propone la implementación de aprendizaje semisupervisado.

3. Datos crudos sin procesar.
    El dataset suminstrado contine datos crudos, es decrir, datos que se reccogen de una determinad fuente y que no han sido sujetos al procesamiento o manipulación. 
    PAra esto es necesario aplicar Feature Engineering. Este es el proceso de transformar datos sin procesar en features que representan mejor el problema subyacente a los modelos predictivos y decribiban la estructura inherentes a los datos, lo que resulta en una mayor precisión del modelo en datos invisibles.
    Es crucial aondar mas en este proceso, antes de tratar de mejorar los resultados del modelo mediante la incorporación de modelos más complejos y la optimización de parametros, como dice la frace "Garbage in, garbage out". Por lo cual, es importante gastar mas tiempo en construir good features para tener mejorres resultados, a pesar de que no sean los mas optimos.
    Con base a esto, uan gran parte del code review se centrara en ampliar la parte de Feature Engineering.
    
Finalmente, con todo lo comentado anterior, pude validar que las preocupaciones de los stackholders son totalmente validas. Por lo cual, acontinuación presento mi propuesa ya a nivel de codigo e implementación para este problema, la cual sigue los siguientes pasos y tecnicas a aplicar:
   <img src="images/machine_learning_pipeline.png">

In [1]:
import pandas as pd
from pandas_profiling import ProfileReport
import numpy as np
import os
import datetime
import logging
logging.basicConfig(format='%(asctime)s - %(levelname)s - %(message)s', level=logging.INFO)

import plotly.graph_objects as go
from sksurv.nonparametric import kaplan_meier_estimator
from sksurv.ensemble import RandomSurvivalForest
import eli5
from eli5.sklearn import PermutationImportance
import tensorflow as tf
from tensorflow import feature_column
from sklearn.model_selection import StratifiedShuffleSplit

from src.auxiliary_functions import transform_tuple_target 



In [2]:
ROOT_PATH = os.getcwd()
DATA_PATH = os.path.join(ROOT_PATH, 'data')

CATEGORICAL_FEATURES = ['car_type', 'color', 'transmission', 'body_type', 'card_brand']
NUMERICAL_FEATURES = ['km', 'average_price', 'antiquity', 'diff_price', 'diff_price_perc']

In [3]:
def get_extract_features(df):
    
    df = df.rename(columns={'first_price': 'price'})
    df['diff_price'] = df['average_price'] - df['price']
    df['diff_price_perc'] = (df['average_price'] - df['price'])/df['average_price']
    
    df[['card_brand', 'car_type', 'C']] = df_detail_cars['car_type'].str.split('_', 2, expand=True)
    
    current_year = datetime.datetime.now().year
    df['antiquity'] = current_year - df.year
    
    df = df.drop(columns=['C', 'year'])
    
    return df

def change_numeric_column_types(df):
    df[['average_price', 'price']] = df[['average_price', 'price']].astype('float')
    df[['antiquity', 'km']] = df[['antiquity', 'km']].astype('int32')
    return df

# Code to Review

In [4]:
logging.info('Starting my code review')

2021-05-29 18:47:53,078 - INFO - Starting my code review


## Data Ingestion

Este paso del codigo abarca el proceso de ingesta de datos. Este proceso consiste en cargar los registros de datos provenientes de un conjunto de archivos tipo csv para importarlos en un dataframe de Pandas. Este dataframe consolida los datos necesarios para alimentar el modelo. 

In [5]:
logging.info('Loading the historical data with the characteristics of the cars')
df_cars = pd.read_csv(os.path.join(DATA_PATH, 'cars.csv'))
df_car_type_characteristics = pd.read_csv(os.path.join(DATA_PATH, 'car_type_characteristics.csv'))
df_detail_cars = pd.merge(df_cars, df_car_type_characteristics, on='car_type', how='left').set_index('car_id')


logging.info('Loading the train cars data')
df_train_cars = pd.read_csv(os.path.join(DATA_PATH, 'train_cars.csv'))
df_train_cars = df_train_cars.sort_values(['car_id', 'day'])

logging.info('Processing the train cars data. This data contains the history of the days in a car listing and the status of the sales process. However, the relevant thing is to extract the listing time and wheter or not it was already sold at his time.')
df_train_cars_sum = df_train_cars.groupby(['car_id']).agg({
    'day': 'count', 
    'price': 'last', 
    'sold': 'last'}
)


logging.info('Loading the test cars data')
df_test_cars = pd.read_csv(os.path.join(DATA_PATH, 'test_cars.csv'))

logging.info('Processing the train cars data. This data contains the history of the days in a car listing and the status of the sales process. However, the relevant thing is to extract the listing time and wheter or not it was already sold at his time.')
df_test_cars_sum = df_test_cars.set_index('car_id')

logging.info('Joining the train and test data set wiht the historical data with the characteristics of the cars')
df_detail_cars_listing_train = df_detail_cars.join(df_train_cars_sum,how='left').\
    join(df_test_cars_sum,how='left').\
    rename(columns={'day': 'DI'})
#df_detail_cars_listing_train = get_extract_features(df_detail_cars_listing_train)
df_detail_cars_listing_train = change_numeric_column_types(df_detail_cars_listing_train)





2021-05-29 18:47:53,089 - INFO - Loading the historical data with the characteristics of the cars
2021-05-29 18:47:53,165 - INFO - Loading the train cars data
/Users/marialanza/Documents/ProjectsML_MF/mfrancys/venv/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (1) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
2021-05-29 18:47:53,348 - INFO - Processing the train cars data. This data contains the history of the days in a car listing and the status of the sales process. However, the relevant thing is to extract the listing time and wheter or not it was already sold at his time.
2021-05-29 18:47:53,395 - INFO - Loading the test cars data
2021-05-29 18:47:53,406 - INFO - Processing the train cars data. This data contains the history of the days in a car listing and the status of the sales process. However, the relevant thing is to extract the listing time 

KeyError: "['antiquity'] not in index"

In [ ]:
df_detail_cars_listing_train

In [58]:
df_test_cars_sum

first_date  first_price
car_id                         
0       2019-08-14       228071
1       2019-09-18       240014
10      2019-11-08       324066
10000   2019-11-07       297417
10001   2019-12-31       934590
...            ...          ...
9989    2019-12-19       701184
9990    2019-10-16      1038960
9991    2019-08-10       258652
9994    2019-06-20       785657
9996    2019-12-28       575997

[11673 rows x 2 columns]

In [36]:
logging.info('Split data to validation model')
X_train_aux = df_train_cars_sum.copy()
y_train_aux = X_train_aux.pop('sold')
sssplit = StratifiedShuffleSplit(n_splits=1, test_size=0.2, random_state=123)
for aux_index, validation_index in sssplit.split(X_train_aux, y_train_aux):
    logging.info(len(validation_index.tolist()))



df_detail_cars.index


Index(['0', '112', '1497', '1891', '1955', '2435', '2645', '3640', '3743',
       '4405',
       ...
       '14019', '15396', '15629', '15855', '16169', '16468', '16971', '17013',
       '18235', '18543'],
      dtype='object', name='car_id', length=20000)

In [37]:
df_detail_cars = df_detail_cars.index.isin(validation_index.tolist())

array([False, False, False, ..., False, False, False])

In [ ]:
logging.info('Joining the train data set wiht the historical data with the characteristics of the cars')
df_detail_cars_listing_train = df_detail_cars.join(df_train_cars_sum,how='left').\
    join(df_test_cars_sum,how='left').\
    rename(columns={'day': 'DI'})
df_detail_cars_listing_train = get_extract_features(df_detail_cars_listing_train)
df_detail_cars_listing_train = change_numeric_column_types(df_detail_cars_listing_train)



## Data Validation

La validación de datos es un proceso donde se produce estadísticas sobre las características de los datos y resalta si una característica contiene un alto porcentaje de valores perdidos o si las características están altamente correlacionadas. Esta es información útil cuando decide qué características deben incluirse en el paso de preprocesamiento y cuál debe ser la forma del preprocesamiento.

### Profile report

In [8]:
profile = ProfileReport(df_detail_cars_listing_train, title="Pandas Profiling Report")
profile.to_widgets()
profile.to_notebook_iframe()
profile.to_file("inventory_day_profile_report.html")

Summarize dataset:   0%|          | 0/27 [00:00<?, ?it/s]

2021-05-29 17:35:09,115 - INFO - Using categorical units to plot a list of strings that are all parsable as floats or dates. If these strings should be plotted as numbers, cast to the appropriate data type before plotting.
2021-05-29 17:35:09,153 - INFO - Using categorical units to plot a list of strings that are all parsable as floats or dates. If these strings should be plotted as numbers, cast to the appropriate data type before plotting.
2021-05-29 17:35:54,647 - INFO - Using categorical units to plot a list of strings that are all parsable as floats or dates. If these strings should be plotted as numbers, cast to the appropriate data type before plotting.
2021-05-29 17:36:19,190 - INFO - Using categorical units to plot a list of strings that are all parsable as floats or dates. If these strings should be plotted as numbers, cast to the appropriate data type before plotting.
2021-05-29 17:36:42,995 - INFO - Using categorical units to plot a list of strings that are all parsable as 

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Una de las técnicas más populares para el analisis de supervivencia es el estimador de Kaplan-Meier. Esta tecnica representa uno de los enfoques no paramétricos más populares utilizado para estimar la función de supervivencia. La representación visual de esta función generalmente se llama curva de Kaplan-Meier y muestra cuál es la probabilidad de supervivencia en un determinado intervalo de tiempo. Una de las limitaciones de esta técnica es que no puede estimar la supervivencia considerando co-variables.

The estimated curve below is a step function, with steps occurring at time points where one or more cars were sold. From the plot we can see that most patients died in the first 200 days, as indicated by the steep slope of the estimated survival function in the first 200 days. Then we see that the longer the inventory lasts, the number of cars sold is reduced.

In [ ]:

def kaplan_meier_estimator_plot(df, action, time):
    time_sold, survival_prob_sold = kaplan_meier_estimator(df[action], df[time])
    fig = go.Figure(go.Scatter(x=time_sold, y=survival_prob_sold, mode='lines', name='lines'))
    fig.update_layout(
        title='The Survival Function',
        xaxis_title='DI - (Days od Inventory)',
        yaxis_title='est. probability of survival $\hat{S}(t)$',
        xaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
        yaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
        plot_bgcolor='white'
    )
    fig.show()
    
def kaplan_meier_estimator_by_statification_plot(df, action, time, statification):
    feature_values = df_detail_cars_listing_train[statification].unique().tolist()
    fig = go.Figure()
    
    for value in feature_values:
        mask = df[feature] == value
        time_sold, survival_prob_sold = kaplan_meier_estimator(df[action][mask], df[time][mask])
        fig.add_trace(go.Scatter(x=time_sold, y=survival_prob_sold, mode='lines', name=value))
    
    fig.update_layout(
        title=f'The Survival Function by Statification - {statification}',
        xaxis_title='DI - (Days od Inventory)',
        yaxis_title='est. probability of survival $\hat{S}(t)$',
        xaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
        yaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
        plot_bgcolor='white'
    )
    fig.show()
    

#kaplan_meier_estimator_plot(df_detail_cars_listing_train, 'sold', 'DI')
#fetures = ['car_type', 'color', 'transmission', 'body_type', 'card_brand']
#for feature in fetures: 
#    kaplan_meier_estimator_by_statification_plot(df_detail_cars_listing_train, 'sold', 'DI', feature)


Antes de comenzar entrenar, es importante determinar cuál es la cantidad de censura para estos datos y graficar los tiempos de supervivencia / censura.

In [ ]:
n_censored = df_detail_cars_listing_train.sold.value_counts()[1] - df_detail_cars_listing_train.sold.value_counts()[0]
print("{}% of records are censored".format(n_censored / df_detail_cars_listing_train.shape[0] * 100))

In [ ]:

df_detail_cars_listing_train_sum = df_detail_cars_listing_train.reset_index().groupby(['sold', 'DI'], as_index=False).agg({'car_id': 'count'})

mask_sold = df_detail_cars_listing_train_sum.sold==True
fig = go.Figure()
fig = go.Figure(data=[
    go.Bar(name='Sold - True', x=df_detail_cars_listing_train_sum.DI, y=df_detail_cars_listing_train_sum.car_id[mask_sold]),
    go.Bar(name='Sold - False', x=df_detail_cars_listing_train_sum.DI, y=df_detail_cars_listing_train_sum.car_id[~mask_sold])
])
# Change the bar mode
fig.update_layout(
    barmode='group',
    title=f'Data',
    xaxis_title='DI - (Days od Inventory)',
    yaxis_title='number of cars',
    xaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
    yaxis=dict(showline=True, linecolor='rgb(204, 204, 204)', linewidth=2),
    plot_bgcolor='white'
)
#fig.show()

## Data Preprocessing

Los datos que se vas a usar para entrenar el modelos de aprendizaje automático se encueentran en formatos que el no pueden consumir. Por ejemplo, las varibes card_brand, body_type, transmission, color y car_type; por lo cual, el modelo requiere una representación numérica de estos valores (por ejemplo, 1 y 0). Esta etapa comprende la apliacion de un conjunto de tecnicas para convertir características en representaciones numéricas consistentes para que el modelo de aprendizaje automático pueda entrenarse con las representaciones numéricas de las características.

In [ ]:
logging.info('A utility method to create a tf.data dataset from a Pandas Dataframe')

def df_to_dataset(dataframe, target, shuffle=True, batch_size=32):
    dataframe = dataframe.copy()
    labels = dataframe.pop(target)
    ds = tf.data.Dataset.from_tensor_slices((dict(dataframe), labels))
    if shuffle:
        ds = ds.shuffle(buffer_size=len(dataframe))
        ds = ds.batch(batch_size)
    return ds

categorical_features = ['car_type', 'color', 'transmission', 'body_type', 'card_brand']
batch_size = 500 # A small batch sized is used for demonstration purposes
train_ds = df_to_dataset(df_detail_cars_listing_train, 'DI', batch_size=batch_size)

for feature_batch, label_batch in train_ds.take(1):
    print('Every feature:', list(feature_batch.keys()))
    print('A batch of ages:', feature_batch['transmission'])
    print('A batch of targets:', label_batch )

In [ ]:
# We will use this batch to demonstrate several types of feature columns
example_batch = next(iter(train_ds))[0]

# We will use this batch to demonstrate several types of feature columns

example_batch 

#### - Numerical Inputs 

In [ ]:

#NUMERIC_FEATURES = ['average_price', 'price']
# We will use this batch to demonstrate several types of feature columns
example_batch = next(iter(train_ds))[0]

# A utility method to create a feature column
# and to transform a batch of data
def demo(feature_column, example_batch):
    feature_layer = layers.DenseFeatures(feature_column)
    print(feature_layer(example_batch).numpy())

def zscore(col):
    mean = 3.04
    std = 1.2
    return (col - mean)/std


#transmission = feature_column.numeric_column('average_price', normalizer_fn=zscore)
transmission = feature_column.numeric_column('average_price', normalizer_fn=zscore)
demo(transmission, example_batch)

#### Bucketized columns -> antiquity and km

A menudo, no desea ingresar un número directamente en el modelo, sino dividir su valor en diferentes categorías según los rangos numéricos. Considere los datos brutos que representan la edad de una persona. En lugar de representar la edad como una columna numérica, podríamos dividir la edad en varios grupos utilizando una columna dividida en grupos. Observe que los valores one-hot a continuación describen con qué rango de edad coincide cada fila.

In [ ]:
NUMERIC_FEATURES = ['antiquity', 'km']

age = feature_column.numeric_column('km')
age_buckets = feature_column.bucketized_column(age, boundaries=[0., 1., 2.])
demo(age_buckets, example_batch)

#### - Categorical Inputs

#### Categorical columns -> Color and transmission

En este conjunto de datos, el tipo se representa como una cadena (por ejemplo, 'Perro' o 'Gato'). No podemos alimentar cadenas directamente a un modelo. En su lugar, primero debemos asignarlos a valores numéricos. Las columnas de vocabulario categórico proporcionan una forma de representar cadenas como un vector de un solo uso (muy parecido a lo que ha visto anteriormente con los depósitos de edad). El vocabulario puede pasarse como una lista usando categorical_column_with_vocabulary_list, o cargarse desde un archivo usando categorical_column_with_vocabulary_file.

In [ ]:
animal_type = feature_column.categorical_column_with_vocabulary_list(
      'transmission', df_detail_cars_listing_train['transmission'].unique())

animal_type_one_hot = feature_column.indicator_column(animal_type)
demo(animal_type_one_hot, example_batch)

#### Embedding columns -> body_type, car_brand and car_type
Supongamos que en lugar de tener solo unas pocas cadenas posibles, tenemos miles (o más) valores por categoría. Por varias razones, a medida que aumenta el número de categorías, no es factible entrenar una red neuronal utilizando codificaciones one-hot. Podemos utilizar una columna de incrustación para superar esta limitación. En lugar de representar los datos como un vector único de muchas dimensiones, una columna de incrustación representa esos datos como un vector denso de menor dimensión en el que cada celda puede contener cualquier número, no solo 0 o 1. El tamaño de la incrustación ( 8, en el ejemplo siguiente) es un parámetro que debe ajustarse.

In [ ]:
# Notice the input to the embedding column is the categorical column
# we previously created
breed1 = feature_column.categorical_column_with_vocabulary_list(
      'car_type', dataframe.car_type.unique())
breed1_embedding = feature_column.embedding_column(breed1, dimension=8)
demo(breed1_embedding, example_batch)

#### Crossed feature columns
La combinación de características en una sola característica, más conocida como cruces de características, permite que un modelo aprenda pesos separados para cada combinación de características. Aquí, crearemos una nueva característica que es el cruce de Edad y Tipo. Tenga en cuenta que la columna_cruzada no crea la tabla completa de todas las combinaciones posibles (que podría ser muy grande). En su lugar, está respaldado por una columna hash, por lo que puede elegir el tamaño de la tabla.

In [ ]:
['car_type', 'color', 'km', 'average_price', 'transmission', 'body_type', 'price', 'sold', 'card_brand', 'antiquity']

### Predictions in Survival Analysis

## Modeling

In [ ]:
y_train = transform_tuple_target(df_detail_cars_listing_train, 'sold', 'days') 
X_train = df_detail_cars_listing_train.drop(columns=['sold', 'days'])
X_train = df_detail_cars_listing_train[['km', 'average_price', 'price']]
X_train

### Training

In [ ]:
random_state = 20

rsf = RandomSurvivalForest(n_estimators=1000,
                           min_samples_split=10,
                           min_samples_leaf=15,
                           max_features="sqrt",
                           n_jobs=-1,
                           random_state=random_state)
rsf.fit(X_train, y_train)

rsf.score(X_test, y_test)



### Permutation-based Feature Importance

In [ ]:
perm = PermutationImportance(rsf, n_iter=15, random_state=random_state)
perm.fit(X_test, y_test)
eli5.show_weights(perm, feature_names=feature_names)

The result shows that the number of positive lymph nodes (pnodes) is by far the most important feature. If its relationship to survival time is removed (by random shuffling), the concordance index on the test data drops on average by 0.0676 points. Again, this agrees with the results from the original Random Survival Forests paper.

In [ ]:
## Report 